## regression

## LVXNN

In [1]:
import time
import numpy as np
import pandas as pd 
import tensorflow as tf
from matplotlib import pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error, mean_squared_error
from sklearn.metrics.pairwise import cosine_similarity
from gaminet.utils import local_visualize
from gaminet.utils import global_visualize_density
from gaminet.utils import feature_importance_visualize
from gaminet.utils import plot_trajectory
from gaminet.utils import plot_regularization
from sklearn.linear_model import LinearRegression
from collections import OrderedDict
import sys
sys.path.append('../../')
from lvxnn.LVXNN import LV_XNN
from lvxnn.DataReader import data_initialize


data= pd.read_csv('data/sim_0.9.csv')
train , test = train_test_split(data,test_size=0.2)

#list1 = data.columns
meta_info = OrderedDict()

meta_info['uf_1']={'type': 'continues','source':'user'}
meta_info['uf_2']={'type': 'continues','source':'user'}
meta_info['uf_3']={'type': 'continues','source':'user'}
meta_info['uf_4']={'type': 'continues','source':'user'}
meta_info['uf_5']={'type': 'continues','source':'user'}
meta_info['if_1']={'type': 'continues','source':'item'}
meta_info['if_2']={'type': 'continues','source':'item'}
meta_info['if_3']={'type': 'continues','source':'item'}
meta_info['if_4']={'type': 'continues','source':'item'}
meta_info['if_5']={'type': 'continues','source':'item'}
meta_info['user_id']={"type":"id",'source':'user'}
meta_info['item_id']={"type":"id",'source':'item'}
meta_info['target']={"type":"target",'source':''}


tr_x, tr_Xi, tr_y , te_x , te_Xi, te_y, meta_info, model_info = data_initialize(train,test,meta_info,"Regression")

def auto_test():
    cold_mae = []
    cold_rmse = []
    warm_mae = []
    warm_rmse = []
    gami_mae = []
    gami_rmse = []

    for times in range(10):
        
        print(times)

        model = LV_XNN(model_info=model_info, meta_info=meta_info, subnet_arch=[8, 16],interact_arch=[20, 10],activation_func=tf.tanh, batch_size=1000, lr_bp=0.01, auto_tune=True,
               interaction_epochs=200,main_effect_epochs=300,tuning_epochs=50,loss_threshold_main=0.01,loss_threshold_inter=0.01,alpha=0.5,
              verbose=True,val_ratio=0.125, early_stop_thres=100,interact_num=10,u_group_num=10,i_group_num=50,scale_ratio=1,n_power_iterations=5,n_oversamples=0,
              mf_training_iters=1,mf_tuning_iters=200,change_mode=True,convergence_threshold=0.001,max_rank=3,shrinkage_value=20,random_state=times)
    
        st_time = time.time()
        model.fit(tr_x,tr_Xi, tr_y)
        ed_time = time.time()
        
        pred = model.predict(te_x, te_Xi)
        
        cold_y = te_y[(te_Xi[:,1] == 'cold') | (te_Xi[:,0] == 'cold')]
        cold_pred = pred[(te_Xi[:,1] == 'cold') | (te_Xi[:,0] == 'cold')]
        warm_y = te_y[(te_Xi[:,1] != 'cold') & (te_Xi[:,0] != 'cold')]
        warm_pred = pred[(te_Xi[:,1] != 'cold') & (te_Xi[:,0] != 'cold')]
    
        cold_mae.append(mean_absolute_error(cold_y,cold_pred))
        cold_rmse.append(mean_squared_error(cold_y,cold_pred)**0.5)
        warm_mae.append(mean_absolute_error(te_y,pred))
        warm_rmse.append(mean_squared_error(te_y,pred)**0.5)
        

        gami_mae.append(mean_absolute_error(te_y,model.final_gam_model.predict(te_x)))
        gami_rmse.append(mean_squared_error(te_y,model.final_gam_model.predict(te_x))**0.5)
        
    i_result = np.array([np.mean(cold_mae),np.mean(cold_rmse),np.mean(warm_mae),np.mean(warm_rmse)]).reshape(1,-1)
    result = pd.DataFrame(i_result,columns=['cold_mae','cold_rmse','warm_mae','warm_rmse'])
    
    g_result = np.array([np.mean(gami_mae),np.mean(gami_rmse)]).reshape(1,-1)
    g_result = pd.DataFrame(g_result,columns=['mae','rmse'])
    
    return result, g_result

results, g_result = (auto_test())
results.to_csv('result/Regression_LVXNN_result.csv',index=None)
g_result.to_csv('result/Regression_gami_result.csv',index=None)

Memory usage of dataframe is 0.86 MB


../..\lvxnn\DataReader.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  df[col] = df[col].astype(np.float16)


Memory usage after optimization is: 0.26 MB
Decreased by 69.6%
Memory usage of dataframe is 0.21 MB
Memory usage after optimization is: 0.07 MB
Decreased by 69.6%
cold start user: 31
cold start item: 325
0
ListWrapper(['uf_1', 'uf_2', 'uf_3', 'uf_4', 'uf_5', 'if_1', 'if_2', 'if_3', 'if_4', 'if_5'])
####################GAMI-Net training start.####################
##########Stage 1: main effect training start.##########
Main effects training epoch: 1, train loss: 4.03647, val loss: 4.17318
Main effects training epoch: 2, train loss: 3.85096, val loss: 4.00052
Main effects training epoch: 3, train loss: 3.64359, val loss: 3.80150
Main effects training epoch: 4, train loss: 3.44775, val loss: 3.59918
Main effects training epoch: 5, train loss: 3.42751, val loss: 3.57220
Main effects training epoch: 6, train loss: 3.40464, val loss: 3.53713
Main effects training epoch: 7, train loss: 3.28767, val loss: 3.39808
Main effects training epoch: 8, train loss: 3.24918, val loss: 3.36456
Main effec

Main effects training epoch: 115, train loss: 1.63439, val loss: 1.58806
Main effects training epoch: 116, train loss: 1.63461, val loss: 1.59551
Main effects training epoch: 117, train loss: 1.63665, val loss: 1.58530
Main effects training epoch: 118, train loss: 1.64104, val loss: 1.60357
Main effects training epoch: 119, train loss: 1.63703, val loss: 1.58892
Main effects training epoch: 120, train loss: 1.62805, val loss: 1.58201
Main effects training epoch: 121, train loss: 1.63502, val loss: 1.58912
Main effects training epoch: 122, train loss: 1.62625, val loss: 1.58362
Main effects training epoch: 123, train loss: 1.62302, val loss: 1.57376
Main effects training epoch: 124, train loss: 1.62426, val loss: 1.57267
Main effects training epoch: 125, train loss: 1.62699, val loss: 1.59006
Main effects training epoch: 126, train loss: 1.62616, val loss: 1.58006
Main effects training epoch: 127, train loss: 1.62163, val loss: 1.57738
Main effects training epoch: 128, train loss: 1.619

Main effects training epoch: 231, train loss: 1.50603, val loss: 1.48619
Main effects training epoch: 232, train loss: 1.51209, val loss: 1.48608
Main effects training epoch: 233, train loss: 1.50594, val loss: 1.48265
Main effects training epoch: 234, train loss: 1.51205, val loss: 1.48716
Main effects training epoch: 235, train loss: 1.51270, val loss: 1.48099
Main effects training epoch: 236, train loss: 1.50722, val loss: 1.49044
Main effects training epoch: 237, train loss: 1.51751, val loss: 1.49989
Main effects training epoch: 238, train loss: 1.51941, val loss: 1.49729
Main effects training epoch: 239, train loss: 1.51111, val loss: 1.47367
Main effects training epoch: 240, train loss: 1.51832, val loss: 1.49752
Main effects training epoch: 241, train loss: 1.50650, val loss: 1.48829
Main effects training epoch: 242, train loss: 1.51101, val loss: 1.49142
Main effects training epoch: 243, train loss: 1.51274, val loss: 1.47653
Main effects training epoch: 244, train loss: 1.514

...

Main effects tuning epoch: 26, train loss: 1.46560, val loss: 1.50178
Main effects tuning epoch: 27, train loss: 1.45413, val loss: 1.49065
Main effects tuning epoch: 28, train loss: 1.45216, val loss: 1.46971
Main effects tuning epoch: 29, train loss: 1.45545, val loss: 1.46990
Main effects tuning epoch: 30, train loss: 1.45303, val loss: 1.49410
Main effects tuning epoch: 31, train loss: 1.45029, val loss: 1.48009
Main effects tuning epoch: 32, train loss: 1.44986, val loss: 1.48447
Main effects tuning epoch: 33, train loss: 1.45986, val loss: 1.49114
Main effects tuning epoch: 34, train loss: 1.44607, val loss: 1.46740
Main effects tuning epoch: 35, train loss: 1.44963, val loss: 1.47168
Main effects tuning epoch: 36, train loss: 1.46293, val loss: 1.49764
Main effects tuning epoch: 37, train loss: 1.45556, val loss: 1.47847
Main effects tuning epoch: 38, train loss: 1.46256, val loss: 1.48655
Main effects tuning epoch: 39, train loss: 1.44878, val loss: 1.47118
Main effects tuning 

Interaction training epoch: 94, train loss: 0.79177, val loss: 0.81656
Interaction training epoch: 95, train loss: 0.79869, val loss: 0.82257
Interaction training epoch: 96, train loss: 0.79005, val loss: 0.80571
Interaction training epoch: 97, train loss: 0.78882, val loss: 0.81165
Interaction training epoch: 98, train loss: 0.78742, val loss: 0.81532
Interaction training epoch: 99, train loss: 0.78550, val loss: 0.80921
Interaction training epoch: 100, train loss: 0.79877, val loss: 0.81277
Interaction training epoch: 101, train loss: 0.79969, val loss: 0.82035
Interaction training epoch: 102, train loss: 0.80018, val loss: 0.82683
Interaction training epoch: 103, train loss: 0.78781, val loss: 0.81363
Interaction training epoch: 104, train loss: 0.79494, val loss: 0.80936
Interaction training epoch: 105, train loss: 0.79205, val loss: 0.81766
Interaction training epoch: 106, train loss: 0.78924, val loss: 0.81813
Interaction training epoch: 107, train loss: 0.79011, val loss: 0.8058

Interaction tuning epoch: 7, train loss: 0.78325, val loss: 0.81124
Interaction tuning epoch: 8, train loss: 0.78784, val loss: 0.81127
Interaction tuning epoch: 9, train loss: 0.77955, val loss: 0.80493
Interaction tuning epoch: 10, train loss: 0.78340, val loss: 0.81003
Interaction tuning epoch: 11, train loss: 0.78505, val loss: 0.80654
Interaction tuning epoch: 12, train loss: 0.78031, val loss: 0.80876
Interaction tuning epoch: 13, train loss: 0.77813, val loss: 0.79985
Interaction tuning epoch: 14, train loss: 0.78314, val loss: 0.81232
Interaction tuning epoch: 15, train loss: 0.78113, val loss: 0.80604
Interaction tuning epoch: 16, train loss: 0.77868, val loss: 0.80557
Interaction tuning epoch: 17, train loss: 0.77809, val loss: 0.79855
Interaction tuning epoch: 18, train loss: 0.77984, val loss: 0.80506
Interaction tuning epoch: 19, train loss: 0.78458, val loss: 0.81650
Interaction tuning epoch: 20, train loss: 0.77764, val loss: 0.80279
Interaction tuning epoch: 21, train l

[SoftImpute] Iter 65: observed MAE=0.271983 validation MAE=0.482390,rank=3
[SoftImpute] Iter 66: observed MAE=0.270789 validation MAE=0.480565,rank=3
[SoftImpute] Iter 67: observed MAE=0.269628 validation MAE=0.478821,rank=3
[SoftImpute] Iter 68: observed MAE=0.268506 validation MAE=0.477064,rank=3
[SoftImpute] Iter 69: observed MAE=0.267432 validation MAE=0.475434,rank=3
[SoftImpute] Iter 70: observed MAE=0.266377 validation MAE=0.473826,rank=3
[SoftImpute] Iter 71: observed MAE=0.265351 validation MAE=0.472285,rank=3
[SoftImpute] Iter 72: observed MAE=0.264354 validation MAE=0.470797,rank=3
[SoftImpute] Iter 73: observed MAE=0.263412 validation MAE=0.469361,rank=3
[SoftImpute] Iter 74: observed MAE=0.262498 validation MAE=0.467961,rank=3
[SoftImpute] Iter 75: observed MAE=0.261612 validation MAE=0.466557,rank=3
[SoftImpute] Iter 76: observed MAE=0.260767 validation MAE=0.465251,rank=3
[SoftImpute] Iter 77: observed MAE=0.259945 validation MAE=0.464000,rank=3
[SoftImpute] Iter 78: obs

[SoftImpute] Iter 176: observed MAE=0.243065 validation MAE=0.433762,rank=3
[SoftImpute] Iter 177: observed MAE=0.243053 validation MAE=0.433730,rank=3
[SoftImpute] Iter 178: observed MAE=0.243040 validation MAE=0.433715,rank=3
[SoftImpute] Iter 179: observed MAE=0.242963 validation MAE=0.433677,rank=3
[SoftImpute] Iter 180: observed MAE=0.242861 validation MAE=0.433625,rank=3
[SoftImpute] Iter 181: observed MAE=0.242786 validation MAE=0.433553,rank=3
[SoftImpute] Iter 182: observed MAE=0.242712 validation MAE=0.433521,rank=3
[SoftImpute] Iter 183: observed MAE=0.242635 validation MAE=0.433472,rank=3
[SoftImpute] Iter 184: observed MAE=0.242582 validation MAE=0.433466,rank=3
[SoftImpute] Iter 185: observed MAE=0.242511 validation MAE=0.433438,rank=3
[SoftImpute] Iter 186: observed MAE=0.242471 validation MAE=0.433387,rank=3
[SoftImpute] Iter 187: observed MAE=0.242432 validation MAE=0.433412,rank=3
[SoftImpute] Iter 188: observed MAE=0.242383 validation MAE=0.433399,rank=3
[SoftImpute]

## xgboost

In [13]:
from xgboost import XGBRegressor
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
import pandas as pd
import numpy as np
from sklearn.metrics import mean_absolute_error, mean_squared_error

data= pd.read_csv('data/sim_0.9.csv')
train , test = train_test_split(data,test_size=0.2)
data,val = train_test_split(train,test_size=0.125)

x=data.iloc[:,:-1].values
y=data.iloc[:,-1].values
x_t = test.iloc[:,:-1].values
y_t = test.iloc[:,-1].values

enc = MinMaxScaler()
x = enc.fit_transform(x)
x_t = enc.fit_transform(x_t)

def auto_test():
    mae = []
    rmse = []
    for times in range(10):
        xgb = XGBRegressor(n_jobs=-1)
        xgb.fit(x,y)
        pred = xgb.predict(x_t)
        
        mae.append(mean_absolute_error(y_t,pred))
        rmse.append(mean_squared_error(y_t,pred)**0.5)

    i_result = np.array([np.mean(mae),np.mean(rmse)]).reshape(1,-1)
    result = pd.DataFrame(i_result,columns=['mae','rmse'])
    
    return result

results = (auto_test())
results.to_csv('result/Regression_xgboost_result.csv',index=None)

## SVD

In [14]:
from surprise import SVD
from surprise import Dataset
from surprise import Reader
from sklearn.model_selection import train_test_split

data= pd.read_csv('data/sim_0.9.csv')
train , test = train_test_split(data,test_size=0.2)
data,val = train_test_split(train,test_size=0.125)

Xi = data.iloc[:,-3:-1].values
y = data.iloc[:,-1].values
Xi_t = test.iloc[:,-3:-1].values
y_t = test.iloc[:,-1].values

tr_ratings_dict = {'itemID': Xi[:,1].tolist(),
                'userID': Xi[:,0].tolist(),
                'rating': y.tolist()}

tr_df = pd.DataFrame(tr_ratings_dict)

# A reader is still needed but only the rating_scale param is requiered.
reader = Reader(rating_scale=(y.min(), y.max()))

# The columns must correspond to user id, item id and ratings (in that order).
tr_data = Dataset.load_from_df(tr_df[['userID', 'itemID', 'rating']], reader)

tr_data = tr_data.build_full_trainset()

def auto_test():
    mae = []
    rmse = []
    for j in range(10):
        model = SVD(n_factors=3)

        model.fit(tr_data)

        pred = []
        
        for i in range(Xi_t.shape[0]):
            pred.append(model.predict(Xi_t[i,0],Xi_t[i,1],Xi_t[i,0]).est)
    
        pred2 = np.array(pred).ravel()

        mae.append(mean_absolute_error(y_t,pred2))
        rmse.append(mean_squared_error(y_t,pred2)**0.5)
    

    i_result = np.array([np.mean(mae),np.mean(rmse)]).reshape(1,-1)
    result = pd.DataFrame(i_result,columns=['mae','rmse'])
    
    return result

results = (auto_test())
results.to_csv('result/Regression_svd_result.csv',index=None)

## deepfm/fm

In [36]:
class config():
# set the path-to-files
    
    TRAIN_FILE = "../simulation/data/sim_0.9.csv"
    SUB_DIR = "./result"
    NUM_SPLITS = 3
    RANDOM_SEED = 2017

# types of columns of the dataset dataframe
    CATEGORICAL_COLS = []
    NUMERIC_COLS = ["uf_1", "uf_2", "uf_3", "uf_4", "uf_5", "if_1", "if_2", "if_3", "if_4", "if_5"]
    IGNORE_COLS = ["target"]
    
import os
import sys
import numpy as np
import pandas as pd
import tensorflow as tf
from matplotlib import pyplot as plt
from sklearn.metrics import make_scorer
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import KFold
from sklearn.metrics import mean_absolute_error,mean_squared_error
from sklearn.model_selection import train_test_split
sys.path.append('../benchmark/deepfm/')
from DataReader import FeatureDictionary, DataParser
from DeepFM import DeepFM


def _load_data():

    dfTrain = pd.read_csv(config.TRAIN_FILE)
    dfTrain , dfTest = train_test_split(dfTrain,test_size=0.2)

    def preprocess(df):        
        cols = [c for c in df.columns if c not in ["target"]]
        return df

    dfTrain = preprocess(dfTrain)
    dfTest = preprocess(dfTest)
    cols = [c for c in dfTrain.columns if c not in ["target"]]


    X_train = dfTrain[cols].values
    y_train = dfTrain["target"].values
    X_test = dfTest[cols].values
    
    ids_test = dfTest["user_id"].values
    idv_test = dfTest["item_id"].values
    y_test = dfTest['target'].values
        
    return dfTrain, dfTest, X_train, y_train, X_test, ids_test,idv_test, y_test


def _run_base_model_dfm(dfTrain, dfTest, folds, dfm_params):
    fd = FeatureDictionary(dfTrain=dfTrain, dfTest=dfTest,
                           numeric_cols=config.NUMERIC_COLS,
                           ignore_cols=config.IGNORE_COLS)
    data_parser = DataParser(feat_dict=fd)
    Xi_train, Xv_train, y_train = data_parser.parse(df=dfTrain, has_label=True)
    Xi_test, Xv_test, ids_test,idv_test = data_parser.parse(df=dfTest)
    
    dfm_params["feature_size"] = fd.feat_dim
    dfm_params["field_size"] = len(Xi_train[0])
    print(dfm_params)

    y_train_meta = np.zeros((dfTrain.shape[0], 1), dtype=float)
    y_test_meta = np.zeros((dfTest.shape[0], 1), dtype=float)
    _get = lambda x, l: [x[i] for i in l]
    gini_results_cv = np.zeros(len(folds), dtype=float)
    gini_results_epoch_train = np.zeros((len(folds), dfm_params["epoch"]), dtype=float)
    gini_results_epoch_valid = np.zeros((len(folds), dfm_params["epoch"]), dtype=float)
    for i, (train_idx, valid_idx) in enumerate(folds):
        Xi_train_, Xv_train_, y_train_ = _get(Xi_train, train_idx), _get(Xv_train, train_idx), _get(y_train, train_idx)
        Xi_valid_, Xv_valid_, y_valid_ = _get(Xi_train, valid_idx), _get(Xv_train, valid_idx), _get(y_train, valid_idx)

        dfm = DeepFM(**dfm_params)
        dfm.fit(Xi_train_, Xv_train_, y_train_, Xi_valid_, Xv_valid_, y_valid_)

        y_train_meta[valid_idx,0] = dfm.predict(Xi_valid_, Xv_valid_)
        y_test_meta[:,0] += dfm.predict(Xi_test, Xv_test)
        
        gini_results_cv[i] = mean_absolute_error(y_valid_, y_train_meta[valid_idx])
        gini_results_epoch_train[i] = dfm.train_result
        gini_results_epoch_valid[i] = dfm.valid_result

    y_test_meta /= float(len(folds))

    # save result
    return y_train_meta, y_test_meta

# load data
dfTrain, dfTest, X_train, y_train, X_test, ids_test ,idv_test, y_test= _load_data()

# folds
folds = list(KFold(n_splits=config.NUM_SPLITS, shuffle=True,
                             random_state=config.RANDOM_SEED).split(X_train, y_train))



# ------------------ DeepFM Model ------------------
# params
dfm_params = {
    "embedding_size": 3,
    "deep_layers": [32, 32],
    "use_deep" : True ,
    "use_fm" : True , 
    "deep_layers_activation": tf.nn.relu,
    "loss_type" : "mse",
    "epoch": 300 ,
    "batch_size": 1024,
    "learning_rate": 0.01,
    "optimizer_type": "adam",
    "batch_norm": 0,
    "batch_norm_decay": 0.995,
    "l2_reg": 0.01,
    "verbose": False,
    "eval_metric": mean_absolute_error,
    "random_seed": config.RANDOM_SEED
}

def auto_test(deep):
    mae = []
    rmse = []
    dfm_params['use_deep']=deep
    
    for i in range(10):
        y_train_dfm, y_test_dfm = _run_base_model_dfm(dfTrain, dfTest, folds, dfm_params)
        mae.append(mean_absolute_error(y_test,y_test_dfm))
        rmse.append(mean_squared_error(y_test,y_test_dfm)**0.5)
    
    i_result = np.array([np.mean(mae),np.mean(rmse)]).reshape(1,-1)
    results = pd.DataFrame(i_result,columns=['mae','rmse'])
    
    return results
result_1 = (auto_test(True))
result_2 = (auto_test(False))
result_1.to_csv('result/Regression_deepfm_result.csv',index=None)
result_2.to_csv('result/Regression_fm_result.csv',index=None)

{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': True, 'use_fm': True, 'deep_layers_activation': <function relu at 0x000002800723B6A8>, 'loss_type': 'mse', 'epoch': 300, 'batch_size': 1024, 'learning_rate': 0.01, 'optimizer_type': 'adam', 'batch_norm': 0, 'batch_norm_decay': 0.995, 'l2_reg': 0.01, 'verbose': False, 'eval_metric': <function mean_absolute_error at 0x000002801B3421E0>, 'random_seed': 2017, 'feature_size': 1110, 'field_size': 12}
{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': True, 'use_fm': True, 'deep_layers_activation': <function relu at 0x000002800723B6A8>, 'loss_type': 'mse', 'epoch': 300, 'batch_size': 1024, 'learning_rate': 0.01, 'optimizer_type': 'adam', 'batch_norm': 0, 'batch_norm_decay': 0.995, 'l2_reg': 0.01, 'verbose': False, 'eval_metric': <function mean_absolute_error at 0x000002801B3421E0>, 'random_seed': 2017, 'feature_size': 1110, 'field_size': 12}
{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': True, 'use_fm': True, 'deep

{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': False, 'use_fm': True, 'deep_layers_activation': <function relu at 0x000002800723B6A8>, 'loss_type': 'mse', 'epoch': 300, 'batch_size': 1024, 'learning_rate': 0.01, 'optimizer_type': 'adam', 'batch_norm': 0, 'batch_norm_decay': 0.995, 'l2_reg': 0.01, 'verbose': False, 'eval_metric': <function mean_absolute_error at 0x000002801B3421E0>, 'random_seed': 2017, 'feature_size': 1110, 'field_size': 12}
{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': False, 'use_fm': True, 'deep_layers_activation': <function relu at 0x000002800723B6A8>, 'loss_type': 'mse', 'epoch': 300, 'batch_size': 1024, 'learning_rate': 0.01, 'optimizer_type': 'adam', 'batch_norm': 0, 'batch_norm_decay': 0.995, 'l2_reg': 0.01, 'verbose': False, 'eval_metric': <function mean_absolute_error at 0x000002801B3421E0>, 'random_seed': 2017, 'feature_size': 1110, 'field_size': 12}


## classification

## LVXNN

In [3]:
import time
import numpy as np
import pandas as pd 
import tensorflow as tf
from matplotlib import pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_auc_score, log_loss
from sklearn.metrics.pairwise import cosine_similarity
from gaminet.utils import local_visualize
from gaminet.utils import global_visualize_density
from gaminet.utils import feature_importance_visualize
from gaminet.utils import plot_trajectory
from gaminet.utils import plot_regularization
from sklearn.linear_model import LinearRegression
from collections import OrderedDict
import sys
sys.path.append('../../')
from lvxnn.LVXNN import LV_XNN
from lvxnn.DataReader import data_initialize

data= pd.read_csv('data/sim_binary_0.9.csv')
train , test = train_test_split(data,test_size=0.2,random_state = 0)

#list1 = data.columns
meta_info = OrderedDict()

meta_info['uf_1']={'type': 'continues','source':'user'}
meta_info['uf_2']={'type': 'continues','source':'user'}
meta_info['uf_3']={'type': 'continues','source':'user'}
meta_info['uf_4']={'type': 'continues','source':'user'}
meta_info['uf_5']={'type': 'continues','source':'user'}
meta_info['if_1']={'type': 'continues','source':'item'}
meta_info['if_2']={'type': 'continues','source':'item'}
meta_info['if_3']={'type': 'continues','source':'item'}
meta_info['if_4']={'type': 'continues','source':'item'}
meta_info['if_5']={'type': 'continues','source':'item'}
meta_info['user_id']={"type":"id",'source':'user'}
meta_info['item_id']={"type":"id",'source':'item'}
meta_info['target']={"type":"target",'source':''}


tr_x, tr_Xi, tr_y , te_x , te_Xi, te_y, meta_info, model_info = data_initialize(train,test,meta_info,"Classification")

def auto_test():
    cold_auc = []
    cold_logloss = []
    warm_auc = []
    warm_logloss = []
    gami_auc = []
    gami_logloss = []

    for times in range(10):
        
        print(times)


        model = LV_XNN(model_info=model_info, meta_info=meta_info, subnet_arch=[8, 16],interact_arch=[20, 10],activation_func=tf.tanh, batch_size=1000, lr_bp=0.01, auto_tune=False,
               interaction_epochs=200,main_effect_epochs=300,tuning_epochs=50,loss_threshold_main=0.01,loss_threshold_inter=0.01,alpha=1,
              verbose=True,val_ratio=0.125, early_stop_thres=100,interact_num=10,u_group_num=20,i_group_num=50,scale_ratio=0.84,n_power_iterations=5,n_oversamples=0,
              mf_training_iters=1,mf_tuning_iters=100,change_mode=True,convergence_threshold=0.001,max_rank=3,shrinkage_value=20,random_state=times,combine_range=0.98)
    
        st_time = time.time()
        model.fit(tr_x,tr_Xi, tr_y)
        ed_time = time.time()
        
        pred = model.predict(te_x, te_Xi)
        
        cold_y = te_y[(te_Xi[:,1] == 'cold') | (te_Xi[:,0] == 'cold')]
        cold_pred = pred[(te_Xi[:,1] == 'cold') | (te_Xi[:,0] == 'cold')]
        warm_y = te_y[(te_Xi[:,1] != 'cold') & (te_Xi[:,0] != 'cold')]
        warm_pred = pred[(te_Xi[:,1] != 'cold') & (te_Xi[:,0] != 'cold')]
    
        cold_auc.append(roc_auc_score(cold_y,cold_pred))
        cold_logloss.append(log_loss(cold_y,cold_pred))
        warm_auc.append(roc_auc_score(warm_y,warm_pred))
        warm_logloss.append(log_loss(warm_y,warm_pred))
        gami_auc.append(roc_auc_score(te_y,model.final_gam_model.predict(te_x)))
        gami_logloss.append(log_loss(te_y,model.final_gam_model.predict(te_x)))
        
    i_result = np.array([np.mean(cold_auc),np.mean(cold_logloss),np.mean(warm_auc),np.mean(warm_logloss)]).reshape(1,-1)
    result = pd.DataFrame(i_result,columns=['cold_auc','cold_logloss','warm_auc','warm_logloss'])
    
    g_result = np.array([np.mean(gami_auc),np.mean(gami_logloss)]).reshape(1,-1)
    g_result = pd.DataFrame(g_result,columns=['auc','logloss'])
    
    return result, g_result

results, g_result = (auto_test())
results.to_csv('result/Classification_LVXNN_result.csv',index=None)
g_result.to_csv('result/Classification_gami_result.csv',index=None)

Memory usage of dataframe is 0.86 MB


../..\lvxnn\DataReader.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  df[col] = df[col].astype(np.float16)


Memory usage after optimization is: 0.26 MB
Decreased by 69.6%
Memory usage of dataframe is 0.21 MB
Memory usage after optimization is: 0.07 MB
Decreased by 69.6%
cold start user: 36
cold start item: 317
0
ListWrapper(['uf_1', 'uf_2', 'uf_3', 'uf_4', 'uf_5', 'if_1', 'if_2', 'if_3', 'if_4', 'if_5'])
####################GAMI-Net training start.####################
##########Stage 1: main effect training start.##########
Main effects training epoch: 1, train loss: 0.68318, val loss: 0.68192
Main effects training epoch: 2, train loss: 0.67724, val loss: 0.67807
Main effects training epoch: 3, train loss: 0.67035, val loss: 0.67239
Main effects training epoch: 4, train loss: 0.66391, val loss: 0.66654
Main effects training epoch: 5, train loss: 0.65041, val loss: 0.65054
Main effects training epoch: 6, train loss: 0.62260, val loss: 0.61929
Main effects training epoch: 7, train loss: 0.58024, val loss: 0.57432
Main effects training epoch: 8, train loss: 0.54720, val loss: 0.53681
Main effec

Main effects training epoch: 109, train loss: 0.51682, val loss: 0.50096
Main effects training epoch: 110, train loss: 0.51693, val loss: 0.50167
Main effects training epoch: 111, train loss: 0.51671, val loss: 0.50182
Main effects training epoch: 112, train loss: 0.51688, val loss: 0.50161
Main effects training epoch: 113, train loss: 0.51698, val loss: 0.50128
Main effects training epoch: 114, train loss: 0.51709, val loss: 0.50115
Main effects training epoch: 115, train loss: 0.51748, val loss: 0.50244
Main effects training epoch: 116, train loss: 0.51737, val loss: 0.50229
Main effects training epoch: 117, train loss: 0.51675, val loss: 0.50288
Main effects training epoch: 118, train loss: 0.51650, val loss: 0.50089
Main effects training epoch: 119, train loss: 0.51679, val loss: 0.50204
Main effects training epoch: 120, train loss: 0.51664, val loss: 0.50211
Main effects training epoch: 121, train loss: 0.51670, val loss: 0.50227
Main effects training epoch: 122, train loss: 0.516

Main effects tuning epoch: 30, train loss: 0.51600, val loss: 0.50229
Main effects tuning epoch: 31, train loss: 0.51550, val loss: 0.50323
Main effects tuning epoch: 32, train loss: 0.51546, val loss: 0.50104
Main effects tuning epoch: 33, train loss: 0.51535, val loss: 0.50236
Main effects tuning epoch: 34, train loss: 0.51519, val loss: 0.50118
Main effects tuning epoch: 35, train loss: 0.51491, val loss: 0.50257
Main effects tuning epoch: 36, train loss: 0.51491, val loss: 0.50182
Main effects tuning epoch: 37, train loss: 0.51516, val loss: 0.50071
Main effects tuning epoch: 38, train loss: 0.51511, val loss: 0.50194
Main effects tuning epoch: 39, train loss: 0.51511, val loss: 0.50230
Main effects tuning epoch: 40, train loss: 0.51584, val loss: 0.50414
Main effects tuning epoch: 41, train loss: 0.51531, val loss: 0.50065
Main effects tuning epoch: 42, train loss: 0.51515, val loss: 0.50337
Main effects tuning epoch: 43, train loss: 0.51471, val loss: 0.50169
Main effects tuning 

...

Interaction training epoch: 187, train loss: 0.22661, val loss: 0.29056
Interaction training epoch: 188, train loss: 0.23080, val loss: 0.30164
Interaction training epoch: 189, train loss: 0.22038, val loss: 0.28479
Interaction training epoch: 190, train loss: 0.22638, val loss: 0.29376
Interaction training epoch: 191, train loss: 0.22482, val loss: 0.28472
Interaction training epoch: 192, train loss: 0.22470, val loss: 0.29453
Interaction training epoch: 193, train loss: 0.22504, val loss: 0.28936
Interaction training epoch: 194, train loss: 0.22130, val loss: 0.28942
Interaction training epoch: 195, train loss: 0.22154, val loss: 0.28426
Interaction training epoch: 196, train loss: 0.22168, val loss: 0.29193
Interaction training epoch: 197, train loss: 0.21950, val loss: 0.28586
Interaction training epoch: 198, train loss: 0.22612, val loss: 0.29071
Interaction training epoch: 199, train loss: 0.22341, val loss: 0.29090
Interaction training epoch: 200, train loss: 0.22376, val loss: 

C:\Users\64161\Anaconda3\lib\site-packages\numpy\core\fromnumeric.py:3118: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
C:\Users\64161\Anaconda3\lib\site-packages\numpy\core\_methods.py:78: RuntimeWarning: invalid value encountered in true_divide
  ret, rcount, out=ret, casting='unsafe', subok=False)


[SoftImpute] Iter 1: observed BCE=0.200385 validation BCE=0.278800,rank=3
[SoftImpute] Iter 2: observed BCE=0.196692 validation BCE=0.277741,rank=3
[SoftImpute] Iter 3: observed BCE=0.194228 validation BCE=0.276850,rank=3
[SoftImpute] Iter 4: observed BCE=0.192475 validation BCE=0.276358,rank=3
[SoftImpute] Iter 5: observed BCE=0.191143 validation BCE=0.275732,rank=3
[SoftImpute] Iter 6: observed BCE=0.190166 validation BCE=0.275317,rank=3
[SoftImpute] Iter 7: observed BCE=0.189387 validation BCE=0.274591,rank=3
[SoftImpute] Iter 8: observed BCE=0.189070 validation BCE=0.274604,rank=3
[SoftImpute] Iter 9: observed BCE=0.188555 validation BCE=0.274020,rank=3
[SoftImpute] Iter 10: observed BCE=0.188297 validation BCE=0.273700,rank=3
[SoftImpute] Iter 11: observed BCE=0.188118 validation BCE=0.273364,rank=3
[SoftImpute] Iter 12: observed BCE=0.187891 validation BCE=0.273115,rank=3
[SoftImpute] Iter 13: observed BCE=0.187783 validation BCE=0.272900,rank=3
[SoftImpute] Iter 14: observed BCE

C:\Users\64161\Anaconda3\lib\site-packages\numpy\core\fromnumeric.py:3118: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
C:\Users\64161\Anaconda3\lib\site-packages\numpy\core\_methods.py:78: RuntimeWarning: invalid value encountered in true_divide
  ret, rcount, out=ret, casting='unsafe', subok=False)


[SoftImpute] Iter 18: observed BCE=0.187916 validation BCE=0.271876,rank=3
[SoftImpute] Iter 19: observed BCE=0.187928 validation BCE=0.272343,rank=3
[SoftImpute] Iter 20: observed BCE=0.187837 validation BCE=0.272267,rank=3
[SoftImpute] Iter 21: observed BCE=0.187585 validation BCE=0.272333,rank=3
[SoftImpute] Iter 22: observed BCE=0.187717 validation BCE=0.271983,rank=3
[SoftImpute] Iter 23: observed BCE=0.187339 validation BCE=0.271881,rank=3
[SoftImpute] Iter 24: observed BCE=0.187288 validation BCE=0.271682,rank=3
[SoftImpute] Iter 25: observed BCE=0.186986 validation BCE=0.271655,rank=3
[SoftImpute] Iter 26: observed BCE=0.186852 validation BCE=0.271623,rank=3
[SoftImpute] Iter 27: observed BCE=0.187607 validation BCE=0.270468,rank=3
[SoftImpute] Iter 28: observed BCE=0.188308 validation BCE=0.270170,rank=3
[SoftImpute] Iter 29: observed BCE=0.188557 validation BCE=0.269719,rank=3
[SoftImpute] Iter 30: observed BCE=0.189559 validation BCE=0.268979,rank=3
[SoftImpute] Iter 31: obs

## xgboost

In [6]:
from xgboost import XGBClassifier
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
import pandas as pd
import numpy as np
from sklearn.metrics import roc_auc_score, log_loss

data= pd.read_csv('data/sim_binary_0.9.csv')
train , test = train_test_split(data,test_size=0.2,random_state=0)
data,val = train_test_split(train,test_size=0.125,random_state=1)
data = data.drop(['user_id','item_id'],1)
test = test.drop(['user_id','item_id'],1)
x=data.iloc[:,:-1].values
y=data.iloc[:,-1].values
x_t = test.iloc[:,:-1].values
y_t = test.iloc[:,-1].values

enc = MinMaxScaler()
x = enc.fit_transform(x)
x_t = enc.fit_transform(x_t)

def auto_test():
    auc = []
    logloss = []
    for times in range(10):
        xgb = XGBClassifier(n_jobs=-1)
        xgb.fit(x,y)
        pred = xgb.predict_proba(x_t)
        
        auc.append(roc_auc_score(y_t,pred[:,1]))
        logloss.append(log_loss(y_t,pred[:,1]))

    i_result = np.array([np.mean(auc),np.mean(logloss)]).reshape(1,-1)
    result = pd.DataFrame(i_result,columns=['auc','logloss'])
    
    return result

results = (auto_test())
results.to_csv('result/Classification_xgboost_result.csv',index=None)

## SVD

In [8]:
from surprise import SVD
from surprise import Dataset
from surprise import Reader
from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_auc_score, log_loss

data= pd.read_csv('data/sim_binary_0.9.csv')
train , test = train_test_split(data,test_size=0.2,random_state=0)
data,val = train_test_split(train,test_size=0.125)

Xi = data.iloc[:,-3:-1].values
y = data.iloc[:,-1].values
Xi_t = test.iloc[:,-3:-1].values
y_t = test.iloc[:,-1].values

tr_ratings_dict = {'itemID': Xi[:,1].tolist(),
                'userID': Xi[:,0].tolist(),
                'rating': y.tolist()}

tr_df = pd.DataFrame(tr_ratings_dict)

# A reader is still needed but only the rating_scale param is requiered.
reader = Reader(rating_scale=(y.min(), y.max()))

# The columns must correspond to user id, item id and ratings (in that order).
tr_data = Dataset.load_from_df(tr_df[['userID', 'itemID', 'rating']], reader)

tr_data = tr_data.build_full_trainset()

def auto_test():
    auc = []
    logloss = []
    for j in range(10):
        model = SVD(n_factors=3)

        model.fit(tr_data)

        pred = []
        
        for i in range(Xi_t.shape[0]):
            pred.append(model.predict(Xi_t[i,0],Xi_t[i,1],Xi_t[i,0]).est)
    
        pred2 = np.array(pred).ravel()

        auc.append(roc_auc_score(y_t,pred2))
        logloss.append(log_loss(y_t,pred2))
    
    i_result = np.array([np.mean(auc),np.mean(logloss)]).reshape(1,-1)
    result = pd.DataFrame(i_result,columns=['auc','logloss'])
    
    return result

results = (auto_test())
results.to_csv('result/Classification_svd_result.csv',index=None)

## deepfm

In [7]:
class config():
# set the path-to-files
    
    TRAIN_FILE = "../simulation/data/sim_binary_0.9.csv"
    SUB_DIR = "./result"
    NUM_SPLITS = 3
    RANDOM_SEED = 2017

# types of columns of the dataset dataframe
    CATEGORICAL_COLS = []
    NUMERIC_COLS = ["uf_1", "uf_2", "uf_3", "uf_4", "uf_5", "if_1", "if_2", "if_3", "if_4", "if_5"]
    IGNORE_COLS = ["target"]
    
import os
import sys
import numpy as np
import pandas as pd
import tensorflow as tf
from matplotlib import pyplot as plt
from sklearn.metrics import make_scorer
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import KFold
from sklearn.metrics import roc_auc_score,log_loss, mean_absolute_error
from sklearn.model_selection import train_test_split
sys.path.append('../benchmark/deepfm/')
from DataReader import FeatureDictionary, DataParser
from DeepFM import DeepFM


def _load_data():

    dfTrain = pd.read_csv(config.TRAIN_FILE)
    dfTrain , dfTest = train_test_split(dfTrain,test_size=0.2,random_state=0)

    def preprocess(df):        
        cols = [c for c in df.columns if c not in ["target"]]
        return df

    dfTrain = preprocess(dfTrain)
    dfTest = preprocess(dfTest)
    cols = [c for c in dfTrain.columns if c not in ["target"]]


    X_train = dfTrain[cols].values
    y_train = dfTrain["target"].values
    X_test = dfTest[cols].values
    
    ids_test = dfTest["user_id"].values
    idv_test = dfTest["item_id"].values
    y_test = dfTest['target'].values
        
    return dfTrain, dfTest, X_train, y_train, X_test, ids_test,idv_test, y_test


def _run_base_model_dfm(dfTrain, dfTest, folds, dfm_params):
    fd = FeatureDictionary(dfTrain=dfTrain, dfTest=dfTest,
                           numeric_cols=config.NUMERIC_COLS,
                           ignore_cols=config.IGNORE_COLS)
    data_parser = DataParser(feat_dict=fd)
    Xi_train, Xv_train, y_train = data_parser.parse(df=dfTrain, has_label=True)
    Xi_test, Xv_test, ids_test,idv_test = data_parser.parse(df=dfTest)
    
    dfm_params["feature_size"] = fd.feat_dim
    dfm_params["field_size"] = len(Xi_train[0])
    print(dfm_params)

    y_train_meta = np.zeros((dfTrain.shape[0], 1), dtype=float)
    y_test_meta = np.zeros((dfTest.shape[0], 1), dtype=float)
    _get = lambda x, l: [x[i] for i in l]
    gini_results_cv = np.zeros(len(folds), dtype=float)
    gini_results_epoch_train = np.zeros((len(folds), dfm_params["epoch"]), dtype=float)
    gini_results_epoch_valid = np.zeros((len(folds), dfm_params["epoch"]), dtype=float)
    for i, (train_idx, valid_idx) in enumerate(folds):
        Xi_train_, Xv_train_, y_train_ = _get(Xi_train, train_idx), _get(Xv_train, train_idx), _get(y_train, train_idx)
        Xi_valid_, Xv_valid_, y_valid_ = _get(Xi_train, valid_idx), _get(Xv_train, valid_idx), _get(y_train, valid_idx)

        dfm = DeepFM(**dfm_params)
        dfm.fit(Xi_train_, Xv_train_, y_train_, Xi_valid_, Xv_valid_, y_valid_)

        y_train_meta[valid_idx,0] = dfm.predict(Xi_valid_, Xv_valid_)
        y_test_meta[:,0] += dfm.predict(Xi_test, Xv_test)
        
        gini_results_cv[i] = mean_absolute_error(y_valid_, y_train_meta[valid_idx])
        gini_results_epoch_train[i] = dfm.train_result
        gini_results_epoch_valid[i] = dfm.valid_result

    y_test_meta /= float(len(folds))

    # save result
    return y_train_meta, y_test_meta

# load data
dfTrain, dfTest, X_train, y_train, X_test, ids_test ,idv_test, y_test= _load_data()

# folds
folds = list(KFold(n_splits=config.NUM_SPLITS, shuffle=True,
                             random_state=config.RANDOM_SEED).split(X_train, y_train))



# ------------------ DeepFM Model ------------------
# params
dfm_params = {
    "embedding_size": 3,
    "deep_layers": [32, 32],
    "use_deep" : True ,
    "use_fm" : True , 
    "deep_layers_activation": tf.nn.relu,
    "loss_type" : "logloss",
    "epoch": 100 ,
    "batch_size": 1024,
    "learning_rate": 0.01,
    "optimizer_type": "adam",
    "batch_norm": 0,
    "batch_norm_decay": 0.995,
    "l2_reg": 0.01,
    "verbose": False,
    "eval_metric": log_loss,
    "random_seed": config.RANDOM_SEED
}

def auto_test(deep):
    auc = []
    logloss = []
    dfm_params['use_deep']=deep
    
    for i in range(10):
        dfm_params['random_seed']=i
        y_train_dfm, y_test_dfm = _run_base_model_dfm(dfTrain, dfTest, folds, dfm_params)
        auc.append(roc_auc_score(y_test,y_test_dfm))
        logloss.append(log_loss(y_test,y_test_dfm))
    
    i_result = np.array([np.mean(auc),np.mean(logloss)]).reshape(1,-1)
    results = pd.DataFrame(i_result,columns=['auc','logloss'])
    
    return results
result_1 = (auto_test(True))
result_2 = (auto_test(False))
result_1.to_csv('result/Classification_deepfm_result.csv',index=None)
result_2.to_csv('result/Classification_fm_result.csv',index=None)

W0614 23:17:44.934749  9428 deprecation.py:323] From C:\Users\64161\Anaconda3\lib\site-packages\tensorflow_core\python\compat\v2_compat.py:65: disable_resource_variables (from tensorflow.python.ops.variable_scope) is deprecated and will be removed in a future version.
Instructions for updating:
non-resource variables are not supported in the long term
W0614 23:17:45.111786  9428 deprecation.py:506] From ../benchmark/deepfm\DeepFM.py:93: calling dropout (from tensorflow.python.ops.nn_ops) with keep_prob is deprecated and will be removed in a future version.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': True, 'use_fm': True, 'deep_layers_activation': <function relu at 0x000001A79E1CF620>, 'loss_type': 'logloss', 'epoch': 100, 'batch_size': 1024, 'learning_rate': 0.01, 'optimizer_type': 'adam', 'batch_norm': 0, 'batch_norm_decay': 0.995, 'l2_reg': 0.01, 'verbose': False, 'eval_metric': <function log_loss at 0x000001A7B23A12F0>, 'random_seed': 0, 'feature_size': 1110, 'field_size': 12}
{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': True, 'use_fm': True, 'deep_layers_activation': <function relu at 0x000001A79E1CF620>, 'loss_type': 'logloss', 'epoch': 100, 'batch_size': 1024, 'learning_rate': 0.01, 'optimizer_type': 'adam', 'batch_norm': 0, 'batch_norm_decay': 0.995, 'l2_reg': 0.01, 'verbose': False, 'eval_metric': <function log_loss at 0x000001A7B23A12F0>, 'random_seed': 1, 'feature_size': 1110, 'field_size': 12}
{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': True, 'use_fm': True, 'deep_layers_activation':

C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: invalid value encountered in multiply
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: invalid value encountered in multiply
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\li

C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: invalid value encountered in multiply
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: invalid value encountered in multiply
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\li

{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': True, 'use_fm': True, 'deep_layers_activation': <function relu at 0x000001A79E1CF620>, 'loss_type': 'logloss', 'epoch': 100, 'batch_size': 1024, 'learning_rate': 0.01, 'optimizer_type': 'adam', 'batch_norm': 0, 'batch_norm_decay': 0.995, 'l2_reg': 0.01, 'verbose': False, 'eval_metric': <function log_loss at 0x000001A7B23A12F0>, 'random_seed': 6, 'feature_size': 1110, 'field_size': 12}
{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': True, 'use_fm': True, 'deep_layers_activation': <function relu at 0x000001A79E1CF620>, 'loss_type': 'logloss', 'epoch': 100, 'batch_size': 1024, 'learning_rate': 0.01, 'optimizer_type': 'adam', 'batch_norm': 0, 'batch_norm_decay': 0.995, 'l2_reg': 0.01, 'verbose': False, 'eval_metric': <function log_loss at 0x000001A7B23A12F0>, 'random_seed': 7, 'feature_size': 1110, 'field_size': 12}
{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': True, 'use_fm': True, 'deep_layers_activation':

...

{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': False, 'use_fm': True, 'deep_layers_activation': <function relu at 0x000001A79E1CF620>, 'loss_type': 'logloss', 'epoch': 100, 'batch_size': 1024, 'learning_rate': 0.01, 'optimizer_type': 'adam', 'batch_norm': 0, 'batch_norm_decay': 0.995, 'l2_reg': 0.01, 'verbose': False, 'eval_metric': <function log_loss at 0x000001A7B23A12F0>, 'random_seed': 7, 'feature_size': 1110, 'field_size': 12}
{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': False, 'use_fm': True, 'deep_layers_activation': <function relu at 0x000001A79E1CF620>, 'loss_type': 'logloss', 'epoch': 100, 'batch_size': 1024, 'learning_rate': 0.01, 'optimizer_type': 'adam', 'batch_norm': 0, 'batch_norm_decay': 0.995, 'l2_reg': 0.01, 'verbose': False, 'eval_metric': <function log_loss at 0x000001A7B23A12F0>, 'random_seed': 8, 'feature_size': 1110, 'field_size': 12}


C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: invalid value encountered in multiply
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: invalid value encountered in multiply
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\li

C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: invalid value encountered in multiply
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: invalid value encountered in multiply
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\li

C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: invalid value encountered in multiply
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: invalid value encountered in multiply
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:2174: RuntimeWarning: divide by zero encountered in log
  loss = -(transformed_labels * np.log(y_pred)).sum(axis=1)
C:\Users\64161\Anaconda3\li

{'embedding_size': 3, 'deep_layers': [32, 32], 'use_deep': False, 'use_fm': True, 'deep_layers_activation': <function relu at 0x000001A79E1CF620>, 'loss_type': 'logloss', 'epoch': 100, 'batch_size': 1024, 'learning_rate': 0.01, 'optimizer_type': 'adam', 'batch_norm': 0, 'batch_norm_decay': 0.995, 'l2_reg': 0.01, 'verbose': False, 'eval_metric': <function log_loss at 0x000001A7B23A12F0>, 'random_seed': 9, 'feature_size': 1110, 'field_size': 12}


## cold test

In [5]:
import time
import numpy as np
import pandas as pd 
import tensorflow as tf
from matplotlib import pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error, mean_squared_error
from sklearn.metrics.pairwise import cosine_similarity
from gaminet.utils import local_visualize
from gaminet.utils import global_visualize_density
from gaminet.utils import feature_importance_visualize
from gaminet.utils import plot_trajectory
from gaminet.utils import plot_regularization
from sklearn.linear_model import LinearRegression
from collections import OrderedDict
import sys
sys.path.append('../../')
from lvxnn.LVXNN import LV_XNN
from lvxnn.DataReader import data_initialize


data= pd.read_csv('data/sim_0.9.csv')
train , test = train_test_split(data,test_size=0.2)

#list1 = data.columns
meta_info = OrderedDict()

meta_info['uf_1']={'type': 'continues','source':'user'}
meta_info['uf_2']={'type': 'continues','source':'user'}
meta_info['uf_3']={'type': 'continues','source':'user'}
meta_info['uf_4']={'type': 'continues','source':'user'}
meta_info['uf_5']={'type': 'continues','source':'user'}
meta_info['if_1']={'type': 'continues','source':'item'}
meta_info['if_2']={'type': 'continues','source':'item'}
meta_info['if_3']={'type': 'continues','source':'item'}
meta_info['if_4']={'type': 'continues','source':'item'}
meta_info['if_5']={'type': 'continues','source':'item'}
meta_info['user_id']={"type":"id",'source':'user'}
meta_info['item_id']={"type":"id",'source':'item'}
meta_info['target']={"type":"target",'source':''}


tr_x, tr_Xi, tr_y , te_x , te_Xi, te_y, meta_info, model_info = data_initialize(train,test,meta_info,"Regression")

def auto_test(alpha):
    cold_mae = []
    cold_rmse = []
    warm_mae = []
    warm_rmse = []
    

    for times in range(10):
        
        print(times)


        model = LV_XNN(model_info=model_info, meta_info=meta_info, subnet_arch=[8, 16],interact_arch=[20, 10],activation_func=tf.tanh, batch_size=1000, lr_bp=0.01, auto_tune=False,
               interaction_epochs=200,main_effect_epochs=300,tuning_epochs=50,loss_threshold_main=0.01,loss_threshold_inter=0.01,alpha=1,
              verbose=True,val_ratio=0.125, early_stop_thres=100,interact_num=10,u_group_num=10,i_group_num=50,scale_ratio=alpha,n_power_iterations=5,n_oversamples=0,
              mf_training_iters=1,mf_tuning_iters=400,change_mode=True,convergence_threshold=0.001,max_rank=3,shrinkage_value=20,random_state=times)
    
        st_time = time.time()
        model.fit(tr_x,tr_Xi, tr_y)
        ed_time = time.time()
        
        pred = model.predict(te_x, te_Xi)
        
        cold_y = te_y[(te_Xi[:,1] == 'cold') | (te_Xi[:,0] == 'cold')]
        cold_pred = pred[(te_Xi[:,1] == 'cold') | (te_Xi[:,0] == 'cold')]
        warm_y = te_y[(te_Xi[:,1] != 'cold') & (te_Xi[:,0] != 'cold')]
        warm_pred = pred[(te_Xi[:,1] != 'cold') & (te_Xi[:,0] != 'cold')]
        
        cold_mae.append(mean_absolute_error(cold_y,cold_pred))
        cold_rmse.append(mean_squared_error(cold_y,cold_pred)**0.5)
        warm_mae.append(mean_absolute_error(te_y,pred))
        warm_rmse.append(mean_squared_error(te_y,pred)**0.5)
        
    i_result = np.array([np.mean(cold_mae),np.mean(cold_rmse),np.mean(warm_mae),np.mean(warm_rmse)]).reshape(1,-1)
    result = pd.DataFrame(i_result,columns=['cold_mae','cold_rmse','warm_mae','warm_rmse'])
    
    return result
lii = [0,0.2,0.4,0.6,0.8,1]
results = (auto_test(alpha) for alpha in lii)
results = pd.concat(results)
results.to_csv('result/wc_test.csv',index=None)

Memory usage of dataframe is 0.86 MB


../..\lvxnn\DataReader.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  df[col] = df[col].astype(np.float16)


Memory usage after optimization is: 0.26 MB
Decreased by 69.6%
Memory usage of dataframe is 0.21 MB
Memory usage after optimization is: 0.07 MB
Decreased by 69.6%
cold start user: 40
cold start item: 329
0
ListWrapper(['uf_1', 'uf_2', 'uf_3', 'uf_4', 'uf_5', 'if_1', 'if_2', 'if_3', 'if_4', 'if_5'])
####################GAMI-Net training start.####################
##########Stage 1: main effect training start.##########
Main effects training epoch: 1, train loss: 4.00643, val loss: 3.98251
Main effects training epoch: 2, train loss: 3.84931, val loss: 3.81429
Main effects training epoch: 3, train loss: 3.64703, val loss: 3.57569
Main effects training epoch: 4, train loss: 3.47427, val loss: 3.36377
Main effects training epoch: 5, train loss: 3.40606, val loss: 3.29867
Main effects training epoch: 6, train loss: 3.36459, val loss: 3.27615
Main effects training epoch: 7, train loss: 3.30277, val loss: 3.21485
Main effects training epoch: 8, train loss: 3.26879, val loss: 3.18237
Main effec

Main effects training epoch: 111, train loss: 1.59706, val loss: 1.69846
Main effects training epoch: 112, train loss: 1.58556, val loss: 1.68967
Main effects training epoch: 113, train loss: 1.57964, val loss: 1.68878
Main effects training epoch: 114, train loss: 1.58525, val loss: 1.69017
Main effects training epoch: 115, train loss: 1.58037, val loss: 1.69121
Main effects training epoch: 116, train loss: 1.58022, val loss: 1.68878
Main effects training epoch: 117, train loss: 1.57283, val loss: 1.67991
Main effects training epoch: 118, train loss: 1.57187, val loss: 1.68510
Main effects training epoch: 119, train loss: 1.57044, val loss: 1.68455
Main effects training epoch: 120, train loss: 1.56814, val loss: 1.68247
Main effects training epoch: 121, train loss: 1.56821, val loss: 1.68650
Main effects training epoch: 122, train loss: 1.56492, val loss: 1.67891
Main effects training epoch: 123, train loss: 1.56535, val loss: 1.68061
Main effects training epoch: 124, train loss: 1.564

Main effects training epoch: 228, train loss: 1.51788, val loss: 1.61524
Main effects training epoch: 229, train loss: 1.51574, val loss: 1.62373
Main effects training epoch: 230, train loss: 1.51377, val loss: 1.61144
Main effects training epoch: 231, train loss: 1.51573, val loss: 1.61865
Main effects training epoch: 232, train loss: 1.51601, val loss: 1.61879
Main effects training epoch: 233, train loss: 1.50940, val loss: 1.61326
Main effects training epoch: 234, train loss: 1.51159, val loss: 1.61631
Main effects training epoch: 235, train loss: 1.51191, val loss: 1.61541
Main effects training epoch: 236, train loss: 1.51836, val loss: 1.61806
Main effects training epoch: 237, train loss: 1.51139, val loss: 1.60918
Main effects training epoch: 238, train loss: 1.51257, val loss: 1.62264
Main effects training epoch: 239, train loss: 1.51528, val loss: 1.61095
Main effects training epoch: 240, train loss: 1.51112, val loss: 1.61551
Main effects training epoch: 241, train loss: 1.509

...

Interaction tuning epoch: 47, train loss: 0.78789, val loss: 0.79451
Interaction tuning epoch: 48, train loss: 0.79437, val loss: 0.79882
Interaction tuning epoch: 49, train loss: 0.78887, val loss: 0.78376
Interaction tuning epoch: 50, train loss: 0.78911, val loss: 0.79385
####################GAMI-Net training finished.####################
time cost: 76.66828918457031
After the gam stage, training error is 0.78911 , validation error is 0.79385
missing value counts: 92883
[SoftImpute] Max Singular Value of X_init = 19.468633
#####mf_training#####
[SoftImpute] Iter 1: observed MAE=0.749429 validation MAE=0.788932,rank=3
[SoftImpute] Iter 1: observed MAE=0.785148 validation MAE=0.790145,rank=3
[SoftImpute] Iter 2: observed MAE=0.783864 validation MAE=0.788697,rank=3
[SoftImpute] Iter 3: observed MAE=0.785087 validation MAE=0.789001,rank=3
[SoftImpute] Iter 4: observed MAE=0.785035 validation MAE=0.789540,rank=3
[SoftImpute] Iter 5: observed MAE=0.785648 validation MAE=0.789846,rank=3
[S

Main effects training epoch: 65, train loss: 1.76280, val loss: 1.74481
Main effects training epoch: 66, train loss: 1.75289, val loss: 1.73550
Main effects training epoch: 67, train loss: 1.75204, val loss: 1.73036
Main effects training epoch: 68, train loss: 1.75216, val loss: 1.73852
Main effects training epoch: 69, train loss: 1.74681, val loss: 1.72774
Main effects training epoch: 70, train loss: 1.74038, val loss: 1.72486
Main effects training epoch: 71, train loss: 1.74344, val loss: 1.71961
Main effects training epoch: 72, train loss: 1.73123, val loss: 1.71218
Main effects training epoch: 73, train loss: 1.73382, val loss: 1.71462
Main effects training epoch: 74, train loss: 1.72889, val loss: 1.70695
Main effects training epoch: 75, train loss: 1.72364, val loss: 1.69997
Main effects training epoch: 76, train loss: 1.72953, val loss: 1.71102
Main effects training epoch: 77, train loss: 1.71547, val loss: 1.69192
Main effects training epoch: 78, train loss: 1.72249, val loss: 

Main effects training epoch: 182, train loss: 1.58123, val loss: 1.60092
Main effects training epoch: 183, train loss: 1.58010, val loss: 1.59740
Main effects training epoch: 184, train loss: 1.57761, val loss: 1.59894
Main effects training epoch: 185, train loss: 1.57997, val loss: 1.59317
Main effects training epoch: 186, train loss: 1.58088, val loss: 1.59644
Main effects training epoch: 187, train loss: 1.57844, val loss: 1.60082
Main effects training epoch: 188, train loss: 1.57553, val loss: 1.58986
Main effects training epoch: 189, train loss: 1.57995, val loss: 1.60038
Main effects training epoch: 190, train loss: 1.57518, val loss: 1.58750
Main effects training epoch: 191, train loss: 1.57839, val loss: 1.60193
Main effects training epoch: 192, train loss: 1.57505, val loss: 1.59138
Main effects training epoch: 193, train loss: 1.57623, val loss: 1.58547
Main effects training epoch: 194, train loss: 1.58293, val loss: 1.60626
Main effects training epoch: 195, train loss: 1.583

Main effects training epoch: 296, train loss: 1.52722, val loss: 1.54064
Main effects training epoch: 297, train loss: 1.52512, val loss: 1.53607
Main effects training epoch: 298, train loss: 1.53591, val loss: 1.53294
Main effects training epoch: 299, train loss: 1.53643, val loss: 1.54739
Main effects training epoch: 300, train loss: 1.52329, val loss: 1.53060
##########Stage 1: main effect training stop.##########
2 main effects are pruned, start tuning.##########
Main effects tuning epoch: 1, train loss: 1.52379, val loss: 1.53053
Main effects tuning epoch: 2, train loss: 1.53079, val loss: 1.54162
Main effects tuning epoch: 3, train loss: 1.52223, val loss: 1.53516
Main effects tuning epoch: 4, train loss: 1.53471, val loss: 1.54545
Main effects tuning epoch: 5, train loss: 1.52439, val loss: 1.54264
Main effects tuning epoch: 6, train loss: 1.52119, val loss: 1.52289
Main effects tuning epoch: 7, train loss: 1.52570, val loss: 1.53474
Main effects tuning epoch: 8, train loss: 1.5

KeyboardInterrupt: 

In [2]:
import time
import numpy as np
import pandas as pd 
import tensorflow as tf
from matplotlib import pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_auc_score,log_loss
from sklearn.metrics.pairwise import cosine_similarity
from gaminet.utils import local_visualize
from gaminet.utils import global_visualize_density
from gaminet.utils import feature_importance_visualize
from gaminet.utils import plot_trajectory
from gaminet.utils import plot_regularization
from sklearn.linear_model import LinearRegression
from collections import OrderedDict
import sys
sys.path.append('../../')
from lvxnn.LVXNN import LV_XNN
from lvxnn.DataReader import data_initialize


data= pd.read_csv('data/sim_binary_0.9.csv')
train , test = train_test_split(data,test_size=0.2,random_state=0)

#list1 = data.columns
meta_info = OrderedDict()

meta_info['uf_1']={'type': 'continues','source':'user'}
meta_info['uf_2']={'type': 'continues','source':'user'}
meta_info['uf_3']={'type': 'continues','source':'user'}
meta_info['uf_4']={'type': 'continues','source':'user'}
meta_info['uf_5']={'type': 'continues','source':'user'}
meta_info['if_1']={'type': 'continues','source':'item'}
meta_info['if_2']={'type': 'continues','source':'item'}
meta_info['if_3']={'type': 'continues','source':'item'}
meta_info['if_4']={'type': 'continues','source':'item'}
meta_info['if_5']={'type': 'continues','source':'item'}
meta_info['user_id']={"type":"id",'source':'user'}
meta_info['item_id']={"type":"id",'source':'item'}
meta_info['target']={"type":"target",'source':''}


tr_x, tr_Xi, tr_y , te_x , te_Xi, te_y, meta_info, model_info = data_initialize(train,test,meta_info,"Classification")

def auto_test(alpha):
    cold_auc = []
    cold_loss = []
    warm_auc = []
    warm_loss = []
    

    for times in range(10):
        
        print(times)


        model = LV_XNN(model_info=model_info, meta_info=meta_info, subnet_arch=[8, 16],interact_arch=[20, 10],activation_func=tf.tanh, batch_size=1000, lr_bp=0.01, auto_tune=False,
               interaction_epochs=200,main_effect_epochs=300,tuning_epochs=50,loss_threshold_main=0.01,loss_threshold_inter=0.01,alpha=1,
              verbose=True,val_ratio=0.125, early_stop_thres=100,interact_num=10,u_group_num=30,i_group_num=50,scale_ratio=alpha,n_power_iterations=5,n_oversamples=0,
              mf_training_iters=1,mf_tuning_iters=100,change_mode=True,convergence_threshold=0.001,max_rank=3,shrinkage_value=20,random_state=times,combine_range=0.98)
    
        st_time = time.time()
        model.fit(tr_x,tr_Xi, tr_y)
        ed_time = time.time()
        
        pred = model.predict(te_x, te_Xi)
        
        cold_y = te_y[(te_Xi[:,1] == 'cold') | (te_Xi[:,0] == 'cold')]
        cold_pred = pred[(te_Xi[:,1] == 'cold') | (te_Xi[:,0] == 'cold')]
        warm_y = te_y[(te_Xi[:,1] != 'cold') & (te_Xi[:,0] != 'cold')]
        warm_pred = pred[(te_Xi[:,1] != 'cold') & (te_Xi[:,0] != 'cold')]
        
        cold_auc.append(roc_auc_score(cold_y,cold_pred))
        cold_loss.append(log_loss(cold_y,cold_pred))
        warm_auc.append(roc_auc_score(te_y,pred))
        warm_loss.append(log_loss(te_y,pred))
        

        
    i_result = np.array([np.mean(cold_auc),np.mean(cold_loss),np.mean(warm_auc),np.mean(warm_loss)]).reshape(1,-1)
    result = pd.DataFrame(i_result,columns=['cold_auc','cold_loss','warm_auc','warm_loss'])
    
    return result

lii = [0,0.2,0.4,0.6,0.8,1]
results = (auto_test(alpha) for alpha in lii)
results = pd.concat(results)
results.to_csv('result/wc_test_class.csv',index=None)

Memory usage of dataframe is 0.86 MB


../..\lvxnn\DataReader.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  df[col] = df[col].astype(np.float16)


Memory usage after optimization is: 0.26 MB
Decreased by 69.6%
Memory usage of dataframe is 0.21 MB
Memory usage after optimization is: 0.07 MB
Decreased by 69.6%
cold start user: 36
cold start item: 317
0
ListWrapper(['uf_1', 'uf_2', 'uf_3', 'uf_4', 'uf_5', 'if_1', 'if_2', 'if_3', 'if_4', 'if_5'])
####################GAMI-Net training start.####################
##########Stage 1: main effect training start.##########
Main effects training epoch: 1, train loss: 0.68318, val loss: 0.68192
Main effects training epoch: 2, train loss: 0.67724, val loss: 0.67807
Main effects training epoch: 3, train loss: 0.67035, val loss: 0.67239
Main effects training epoch: 4, train loss: 0.66391, val loss: 0.66654
Main effects training epoch: 5, train loss: 0.65041, val loss: 0.65054
Main effects training epoch: 6, train loss: 0.62260, val loss: 0.61929
Main effects training epoch: 7, train loss: 0.58024, val loss: 0.57432
Main effects training epoch: 8, train loss: 0.54720, val loss: 0.53681
Main effec

Main effects training epoch: 116, train loss: 0.51737, val loss: 0.50229
Main effects training epoch: 117, train loss: 0.51675, val loss: 0.50288
Main effects training epoch: 118, train loss: 0.51650, val loss: 0.50089
Main effects training epoch: 119, train loss: 0.51679, val loss: 0.50204
Main effects training epoch: 120, train loss: 0.51664, val loss: 0.50211
Main effects training epoch: 121, train loss: 0.51670, val loss: 0.50227
Main effects training epoch: 122, train loss: 0.51695, val loss: 0.50339
Main effects training epoch: 123, train loss: 0.51659, val loss: 0.50129
Main effects training epoch: 124, train loss: 0.51633, val loss: 0.50324
Main effects training epoch: 125, train loss: 0.51613, val loss: 0.50129
Main effects training epoch: 126, train loss: 0.51658, val loss: 0.50223
Main effects training epoch: 127, train loss: 0.51636, val loss: 0.50314
Main effects training epoch: 128, train loss: 0.51642, val loss: 0.50299
Main effects training epoch: 129, train loss: 0.516

Main effects tuning epoch: 41, train loss: 0.51531, val loss: 0.50065
Main effects tuning epoch: 42, train loss: 0.51515, val loss: 0.50337
Main effects tuning epoch: 43, train loss: 0.51471, val loss: 0.50169
Main effects tuning epoch: 44, train loss: 0.51484, val loss: 0.50097
Main effects tuning epoch: 45, train loss: 0.51488, val loss: 0.50235
Main effects tuning epoch: 46, train loss: 0.51479, val loss: 0.50102
Main effects tuning epoch: 47, train loss: 0.51487, val loss: 0.50196
Main effects tuning epoch: 48, train loss: 0.51463, val loss: 0.50183
Main effects tuning epoch: 49, train loss: 0.51469, val loss: 0.50103
Main effects tuning epoch: 50, train loss: 0.51472, val loss: 0.50134
##########Stage 2: interaction training start.##########
Interaction training epoch: 1, train loss: 0.49630, val loss: 0.48952
Interaction training epoch: 2, train loss: 0.33769, val loss: 0.34284
Interaction training epoch: 3, train loss: 0.35128, val loss: 0.36496
Interaction training epoch: 4, tr

...

Main effects tuning epoch: 38, train loss: 0.50657, val loss: 0.50400
Main effects tuning epoch: 39, train loss: 0.50659, val loss: 0.50256
Main effects tuning epoch: 40, train loss: 0.50632, val loss: 0.50253
Main effects tuning epoch: 41, train loss: 0.50603, val loss: 0.50329
Main effects tuning epoch: 42, train loss: 0.50622, val loss: 0.50349
Main effects tuning epoch: 43, train loss: 0.50646, val loss: 0.50175
Main effects tuning epoch: 44, train loss: 0.50628, val loss: 0.50337
Main effects tuning epoch: 45, train loss: 0.50623, val loss: 0.50398
Main effects tuning epoch: 46, train loss: 0.50598, val loss: 0.50309
Main effects tuning epoch: 47, train loss: 0.50625, val loss: 0.50238
Main effects tuning epoch: 48, train loss: 0.50597, val loss: 0.50462
Main effects tuning epoch: 49, train loss: 0.50541, val loss: 0.50240
Main effects tuning epoch: 50, train loss: 0.50550, val loss: 0.50238
##########Stage 2: interaction training start.##########
Interaction training epoch: 1, tr

Interaction training epoch: 103, train loss: 0.23469, val loss: 0.29298
Interaction training epoch: 104, train loss: 0.23612, val loss: 0.29454
Interaction training epoch: 105, train loss: 0.23845, val loss: 0.29815
Interaction training epoch: 106, train loss: 0.23848, val loss: 0.30360
Interaction training epoch: 107, train loss: 0.23617, val loss: 0.29343
Interaction training epoch: 108, train loss: 0.23898, val loss: 0.30126
Interaction training epoch: 109, train loss: 0.23805, val loss: 0.30199
Interaction training epoch: 110, train loss: 0.23853, val loss: 0.29364
Interaction training epoch: 111, train loss: 0.23500, val loss: 0.29722
Interaction training epoch: 112, train loss: 0.24232, val loss: 0.30874
Interaction training epoch: 113, train loss: 0.23490, val loss: 0.29137
Interaction training epoch: 114, train loss: 0.23576, val loss: 0.29757
Interaction training epoch: 115, train loss: 0.23460, val loss: 0.29390
Interaction training epoch: 116, train loss: 0.23795, val loss: 

Interaction tuning epoch: 17, train loss: 0.22481, val loss: 0.28786
Interaction tuning epoch: 18, train loss: 0.22462, val loss: 0.28037
Interaction tuning epoch: 19, train loss: 0.22566, val loss: 0.28416
Interaction tuning epoch: 20, train loss: 0.22378, val loss: 0.28258
Interaction tuning epoch: 21, train loss: 0.22375, val loss: 0.28170
Interaction tuning epoch: 22, train loss: 0.22561, val loss: 0.28319
Interaction tuning epoch: 23, train loss: 0.22920, val loss: 0.28950
Interaction tuning epoch: 24, train loss: 0.22236, val loss: 0.28384
Interaction tuning epoch: 25, train loss: 0.23033, val loss: 0.28819
Interaction tuning epoch: 26, train loss: 0.22553, val loss: 0.28864
Interaction tuning epoch: 27, train loss: 0.22641, val loss: 0.28500
Interaction tuning epoch: 28, train loss: 0.22460, val loss: 0.28029
Interaction tuning epoch: 29, train loss: 0.22403, val loss: 0.28690
Interaction tuning epoch: 30, train loss: 0.22708, val loss: 0.28584
Interaction tuning epoch: 31, trai

C:\Users\64161\Anaconda3\lib\site-packages\numpy\core\fromnumeric.py:3118: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
C:\Users\64161\Anaconda3\lib\site-packages\numpy\core\_methods.py:78: RuntimeWarning: invalid value encountered in true_divide
  ret, rcount, out=ret, casting='unsafe', subok=False)


[SoftImpute] Iter 1: observed BCE=0.196553 validation BCE=0.279589,rank=3
[SoftImpute] Iter 2: observed BCE=0.189803 validation BCE=0.291466,rank=3
[SoftImpute] Iter 3: observed BCE=0.184868 validation BCE=0.303788,rank=3
[SoftImpute] Iter 4: observed BCE=0.181207 validation BCE=0.314586,rank=3
[SoftImpute] Iter 5: observed BCE=0.178509 validation BCE=0.314670,rank=3
[SoftImpute] Stopped after iteration 5 for lambda=0.069956
final num of user group: 17
final num of item group: 27
change mode state : True
time cost: 1.5417373180389404
After the matrix factor stage, training error is 0.17851, validation error is 0.31467
